# N-gram language modeling

In this notebook we will build an n-gram language model, inspect the conditional probability distributions and try to generate some text.

For tokenization and creating n-grams from tokenized text, I will use utility functions from NLTK.

In [1]:
# using nltk<=3.8.1
from nltk import download, word_tokenize, ngrams # function for generating n-grams
download('punkt') # tokenizer model
# or punkt_tab with nltk>=3.9.1; we did see some issues with that however.

[nltk_data] Downloading package punkt to /home/ucloud/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [2]:
tokens = word_tokenize("this is an example sentence that we will create some n-grams of")

for n in range(2, 5):
    print(f'{n}-GRAMS')
    print(list(ngrams(tokens, n)))
    print()

2-GRAMS
[('this', 'is'), ('is', 'an'), ('an', 'example'), ('example', 'sentence'), ('sentence', 'that'), ('that', 'we'), ('we', 'will'), ('will', 'create'), ('create', 'some'), ('some', 'n-grams'), ('n-grams', 'of')]

3-GRAMS
[('this', 'is', 'an'), ('is', 'an', 'example'), ('an', 'example', 'sentence'), ('example', 'sentence', 'that'), ('sentence', 'that', 'we'), ('that', 'we', 'will'), ('we', 'will', 'create'), ('will', 'create', 'some'), ('create', 'some', 'n-grams'), ('some', 'n-grams', 'of')]

4-GRAMS
[('this', 'is', 'an', 'example'), ('is', 'an', 'example', 'sentence'), ('an', 'example', 'sentence', 'that'), ('example', 'sentence', 'that', 'we'), ('sentence', 'that', 'we', 'will'), ('that', 'we', 'will', 'create'), ('we', 'will', 'create', 'some'), ('will', 'create', 'some', 'n-grams'), ('create', 'some', 'n-grams', 'of')]



## Training a n-gram model

"Training" an n-gram is, in its essence, a task of creating a table of possible _histories_ and their possible _continuations_. In the table, a row corresponds to a probability distribution conditioned on the _history_ by which we can look up the table. There is one column per possible continuation token. Thus, a cell is the probability of some continutation token _w_ **given** history _h_, written as $p(w|h)$.

The table may look something like this:
| _History_ | a     | axe   | bee   | ... |
| --------- | ----- | ----- | ----- | --- |
| (a, nice) | 0     |  .001 | .0005 | ... |
| (can, see)| .03   |  0    | 0     | ... |
| ...       | ...   | ...   | ...   | ... |

In practice, however, such a table will become very sparse, i.e. contain a lot of zeroes. For a more condensed representation, I will create nested dict-structure, like this:
```python
{
    ("a", "nice"): {"axe": .001, "bee": .0005, ...},
    ("can", "see"): {"a": .03, ...},
    ...
}
```

Which allows us to look up a _history_ and get a conditional probability distribution, like this:
```python
ngram_model[("a", "nice")]
```

For the probability of a specific continutation, I would do like this:
```python
ngram_model[("a", "nice")]["bee"]
```




In the cell below, we will set `n` which will be used through the script. Change the value to see how the model works for different `n`s.

In [29]:
n = 3

Let us try to collect n-grams from Gutenberg books. There is `gutenberg` and `gutenberg-nltk` in our common data folder. The latter has more texts and is better cleaned. You can also try on some other data if you'd like.

In [30]:
from glob import glob
from collections import Counter
from tqdm import tqdm  # progress_bar

# a master counter for all n-grams from the data
ngram_counter = Counter()
tokens_total = 0

# iterate over the books and collect n-grams for the counter object
files = glob(f'../../data/gutenberg-nltk/*.txt')
for filename in tqdm(files, desc='Collecting n-grams'):
    with open(filename) as f:
        text = f.read()

    # create tokens and n-grams and count them
    tokens = word_tokenize(text)
    tokens_total += len(tokens)
    book_ngrams = ngrams(tokens, n)

    # add all ngram counts to the master counter by using the update() method
    ngram_counter.update(book_ngrams)

print()
print('Total number of tokens:', tokens_total)
print('Distinct n-grams:', len(ngram_counter))
ngram_counter.most_common(50)


Total number of tokens: 2538838
Distinct n-grams: 1508891


[((',', 'and', 'the'), 3559),
 (('.', "''", '``'), 3263),
 ((',', "''", 'said'), 2583),
 (('of', 'the', 'LORD'), 1622),
 (('the', 'son', 'of'), 1300),
 (('the', 'children', 'of'), 1265),
 ((',', 'saying', ','), 1254),
 (('the', 'LORD', ','), 1166),
 (('out', 'of', 'the'), 1160),
 (('?', "''", '``'), 1101),
 ((',', 'and', 'he'), 931),
 ((',', 'and', 'I'), 910),
 (('the', 'house', 'of'), 906),
 (('him', ',', 'and'), 852),
 ((',', 'and', 'to'), 846),
 ((',', 'and', 'all'), 822),
 (('.', '``', 'I'), 786),
 (('unto', 'him', ','), 759),
 ((';', 'and', 'the'), 750),
 (("''", 'said', 'the'), 748),
 ((',', 'and', 'said'), 747),
 ((',', 'and', 'his'), 702),
 ((',', 'in', 'the'), 685),
 (('children', 'of', 'Israel'), 646),
 ((',', 'and', 'they'), 628),
 (('the', 'land', 'of'), 619),
 ((',', 'and', 'in'), 616),
 (('he', 'said', ','), 615),
 (('unto', 'them', ','), 615),
 (('saith', 'the', 'LORD'), 615),
 (("''", '``', 'I'), 609),
 (('them', ',', 'and'), 605),
 (('the', 'LORD', '.'), 605),
 ((',', 

To create a model which incorporates the idea of _history_ and a continuation, we will create n-grams of size `n`. We then consider the first `n - 1` tokens as history and the n'th word as a continuation that we want to count in order to make a distribution. We first make a model of raw counts and then normalize the values such that they form a probability distribution where the probability values sum to 1.

In [31]:
from collections import defaultdict

# this will be a dict of Counters, i.e. with the structure: {("a", "nice"): Counter({"bee": 731})}
ngram_model_raw = defaultdict(Counter)

for ngram, count in ngram_counter.items():
    history, continuation = ngram[:-1], ngram[-1]
    ngram_model_raw[history][continuation] += count

In [32]:
ngram_model_raw

defaultdict(collections.Counter,
            {('[', 'Sense'): Counter({'and': 1}),
             ('Sense', 'and'): Counter({'Sensibility': 1, 'Secrecie': 1}),
             ('and', 'Sensibility'): Counter({'by': 1}),
             ('Sensibility', 'by'): Counter({'Jane': 1}),
             ('by', 'Jane'): Counter({'Austen': 3, 'herself': 1}),
             ('Jane', 'Austen'): Counter({'1811': 1, '1818': 1, '1816': 1}),
             ('Austen', '1811'): Counter({']': 1}),
             ('1811', ']'): Counter({'CHAPTER': 1}),
             (']', 'CHAPTER'): Counter({'1': 1, '23': 1, '37': 1, 'I': 1}),
             ('CHAPTER', '1'): Counter({'The': 1, 'Loomings': 1, '.': 1}),
             ('1', 'The'): Counter({'family': 1}),
             ('The', 'family'): Counter({'of': 2, ',': 1, 'usages': 1}),
             ('family',
              'of'): Counter({'the': 89,
                      'cousins': 3,
                      'Judah': 2,
                      'that': 2,
                      'Dashwood': 1

What are likely continuations of _in the_? (Assuming here that we are working with a trigram-model)

In [33]:
ngram_model_raw[('in', 'the')].most_common(10)

[('land', 330),
 ('midst', 309),
 ('world', 242),
 ('house', 213),
 ('morning', 167),
 ('day', 163),
 ('sight', 161),
 ('wilderness', 157),
 ('way', 128),
 ('same', 122)]

To estimate conditional probability $p(w|h)$, we divide the occurrence of the specific continuation by the sum total of all possible continutations, for example:
$$
p("juice"|"apple") = \frac{count("apple", "juice")}{\sum_{v \in V}{count("apple", v)}} = \frac{count("apple", "juice")}{count("apple", "juice") + count("apple", "cider") + count("apple", "pie") + ...}
$$

In [34]:
ngram_model = dict()
for ngram, counter in ngram_model_raw.items():
    # normalize counts by dividing it with the total counts for that "history" n-gram
    summed_count = sum(counter.values())
    ngram_model[ngram] = {word: count / summed_count for word, count in counter.items()}

In [35]:
# checking that they sum to 1 - expect rounding errors (assuming here that we are working with a trigram-model)
sum(ngram_model[('in', 'the')].values())

1.0

In [36]:
ngram_model[('in', 'the')]

{'centre': 0.0013274788113958951,
 'discharge': 0.00010211375472276115,
 'violence': 0.00010211375472276115,
 'neighbourhood': 0.002757071377514551,
 'case': 0.002552843868069029,
 'world': 0.0247115286429082,
 'mean': 0.00030634126416828345,
 'house': 0.021750229755948126,
 'man': 0.0007147962830593281,
 'way': 0.013070560604513427,
 'dependent': 0.00010211375472276115,
 'true': 0.0004084550188910446,
 'same': 0.01245787807617686,
 'pleasure': 0.00010211375472276115,
 'agreement': 0.00010211375472276115,
 'performance': 0.00010211375472276115,
 'prospect': 0.00030634126416828345,
 'appearance': 0.00030634126416828345,
 'year': 0.0030634126416828346,
 'spring': 0.0011232513019503727,
 'most': 0.003982436434187685,
 'country': 0.005718370264474625,
 'opinion': 0.00030634126416828345,
 'discovery': 0.0002042275094455223,
 'cottage': 0.0005105687736138058,
 'course': 0.004186663943633207,
 'flushed': 0.00010211375472276115,
 'habit': 0.0016338200755641784,
 'parlour': 0.000204227509445522

## Generation ("inference")
Now that we have our model in place, we can generate text. This is done in roughly the following way:

Start with _seed_, either chosen randomly or by oneself, which corresponds to a _history_ in our model. Then:
1. Look up the seed in the n-gram model to obtain a conditional probability distribution.
2. Then, "draw" a weighted random continutation token.
3. The new history is the tail of the previous history and the newly generated token. Repeat.

In [37]:
import random
seed = random.choice(list(ngram_model.keys()))
# seed = ('I', 'can')
seed

('home', 'comfortable')

In [38]:
#p rint the beginning of the  text: the seed
for word in seed:
    print(word, end='\n')

previous = seed
for i in range(100):
    # conditional probability distribution given the previous n-1 tokens
    next_word_dist = ngram_model[previous]
    
    # create a list of words and their corresponding probabilities (as "weights")
    words = []
    weights = []
    for word, count in next_word_dist.items():
        words.append(word)
        weights.append(count)

    # make a random choice from the word list using the weights
    next_word = random.choices(words, weights=weights)[0]

    print(next_word, end='\n')
    
    # the new history that we should look up is the tail of the previous history and the new token
    previous = previous[1:] + (next_word,)
    

home
comfortable
at
once
proceeded
to
Salt
Hill
.
MR.
and
MRS.
NEWINGTON
,
SALLY
,
the
true
cut-throats
of
the
people
,
to
know
the
man
who
smiles
on
all
kinds
of
musick
,
all
the
people
,
from
the
sky
pitch-black
.
``
A
very
great
trembling
.
He
is
a
purification
for
sin
shall
not
look
so
impassive
hell
's
probable
.
How
did
the
cherubims
within
the
gates
of
Jerusalem
to
Gath
of
the
earth
,
ever
with
her
,
that
very
period
of
our
enemies
might
serve
him
without
feeling
that
they
are
things
creeping
innumerable
,


What tends to happen for larger values of _n_? Try to inspect the model below at different values of _n_. Is it clear why?

In [39]:
ngram_model

{('[', 'Sense'): {'and': 1.0},
 ('Sense', 'and'): {'Sensibility': 0.5, 'Secrecie': 0.5},
 ('and', 'Sensibility'): {'by': 1.0},
 ('Sensibility', 'by'): {'Jane': 1.0},
 ('by', 'Jane'): {'Austen': 0.75, 'herself': 0.25},
 ('Jane', 'Austen'): {'1811': 0.3333333333333333,
  '1818': 0.3333333333333333,
  '1816': 0.3333333333333333},
 ('Austen', '1811'): {']': 1.0},
 ('1811', ']'): {'CHAPTER': 1.0},
 (']', 'CHAPTER'): {'1': 0.25, '23': 0.25, '37': 0.25, 'I': 0.25},
 ('CHAPTER', '1'): {'The': 0.3333333333333333,
  'Loomings': 0.3333333333333333,
  '.': 0.3333333333333333},
 ('1', 'The'): {'family': 1.0},
 ('The', 'family'): {'of': 0.5, ',': 0.25, 'usages': 0.25},
 ('family', 'of'): {'Dashwood': 0.008849557522123894,
  'his': 0.008849557522123894,
  'females': 0.008849557522123894,
  'the': 0.7876106194690266,
  'their': 0.008849557522123894,
  'Judah': 0.017699115044247787,
  'Elimelech': 0.008849557522123894,
  'Matri': 0.008849557522123894,
  'that': 0.017699115044247787,
  'Obededom': 0.008